In [1]:
import torch
import gpytorch
from botorch.models import SingleTaskGP
from botorch.acquisition.analytic import ExpectedImprovement
from botorch.models.transforms.outcome import Standardize
from gpytorch.kernels import ScaleKernel
from gpytorch.mlls import ExactMarginalLogLikelihood
from botorch import fit_gpytorch_model
from botorch.optim.fit import fit_gpytorch_torch # fix Cholecky jitter error
from scipy.stats import norm
from sklearn.decomposition import PCA
import math 
import numpy as np
import matplotlib.pyplot as plt
import h5py
import pickle
import os
import time

# config plot settings
plt.rcParams["font.size"] = 16

## Load Data

In [2]:
# change to: "normalized" => "min_max" and "standardized" => "zscore"
normalization = "normalized" 

In [3]:
###
#  load data: targets and features
###
file = h5py.File("targets_and_{}_features.jld2".format(normalization), "r")

# feature matrix
X = torch.from_numpy(np.transpose(file["X"][:]))
# simulation data (high fidelity)
y = torch.from_numpy(np.transpose(file["gcmc_y"][:]))
# associated simulation costs
cost = torch.from_numpy(np.transpose(file["gcmc_elapsed_time"][:]))

# total number of COFs in data set
nb_COFs = X.shape[0]

In [4]:
###
#  load data: initializing COFs
###
init_cof_ids_file = pickle.load(
                    open('search_results/{}/initializing_cof_ids_{}.pkl'.format(normalization, normalization), 
                         'rb'))

init_cof_ids = init_cof_ids_file['init_cof_ids']

# total number of BO searches to run = number of initializing sets
nb_runs = len(init_cof_ids)

###
#  print info
###
print("raw data - \n\tX:", X.shape)
print("\t\ty:", y.shape)
print("\t\tcost: ", cost.shape)    
    
print("\nEnsure features are normalized - ")
print("max:\n", torch.max(X, 0).values)
print("min:\n", torch.min(X, 0).values)
print("width:\n",torch.max(X, 0).values - torch.min(X, 0).values)

raw data - 
	X: torch.Size([608, 14])
		y: torch.Size([608])
		cost:  torch.Size([608])

Ensure features are normalized - 
max:
 tensor([1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.],
       dtype=torch.float64)
min:
 tensor([0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.],
       dtype=torch.float64)
width:
 tensor([1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.],
       dtype=torch.float64)


In [5]:
X_unsqueezed = X.unsqueeze(1)

## Helper Functions

#### Analysis

In [6]:
# accumulated cost lags the index of the cost_acquired (iteration COF is identified) by 1
def accumulated_cost(cost_acquired):
    nb_iters = len(cost_acquired)
    accumulated_cost = np.zeros(nb_iters)
    accumulated_cost[0] = cost_acquired[0]
    for i in range(1, len(cost_acquired)):
        accumulated_cost[i] = accumulated_cost[i-1] + cost_acquired[i]
    return accumulated_cost

In [7]:
def get_y_maxes_acquired(y_acquired):
    nb_iters = len(y_acquired)
    return [max(y_acquired[:i+1]) for i in range(nb_iters)]      

#### Construct Initial Inputs

In [8]:
# construct feature matrix of acquired points
def build_X_train(ids_acquired):
    return X[ids_acquired, :]

# construct output vector for acquired points
def build_y_train(ids_acquired):
    return y[ids_acquired].unsqueeze(-1)

# construct vector to track accumulated cost of acquired points
def build_cost(ids_acquired):
    return cost[ids_acquired]

In [9]:
# construct and fit GP model
def construct_and_fit_gp_model(X_train, y_train):      
    model = SingleTaskGP(X_train, y_train, outcome_transform=Standardize(m=1))
    mll   = ExactMarginalLogLikelihood(model.likelihood, model)
    fit_gpytorch_model(mll, optimizer=fit_gpytorch_torch)
    return model

#### Bayesian Algorithm

In [10]:
def run_Bayesian_optimization(nb_iterations, initializing_COFs, verbose=False):
    assert nb_iterations > len(initializing_COFs)
    ###
    #  initialize system
    ###
    # select initial COFs for training data
    ids_acquired = initializing_COFs
    
    ###
    #  itterate through remaining budget using BO
    ###
    for i in range(len(initializing_COFs), nb_iterations):
        # construct training data (perform experiments)
        X_train = build_X_train(ids_acquired)
        y_train = build_y_train(ids_acquired)
        
        # fit GP surrogate model
        model = construct_and_fit_gp_model(X_train, y_train)
        
        # compute expected improvement acquisition function
        acq_fn   = ExpectedImprovement(model, best_f=y_train.max().item())
        acq_vals = acq_fn.forward(X.unsqueeze(1))
        
        # identify COF with highest acquisition value currently *not* in training set
        ids_sorted_by_aquisition = acq_vals.argsort(descending=True)
        for id_max in ids_sorted_by_aquisition:
            if not id_max.item() in ids_acquired:
                id_max_acq = id_max.item()
                break
                
        ###
        #  acquire this COF
        ###
        ids_acquired = np.concatenate((ids_acquired, [id_max_acq]))
        if verbose:
            print("BO iteration ", i)
            print("\tacquired COF ", id_max_acq)
            print("\ty = ", y[id_max_acq].item())
    
    # check budget constraint is stisfied
    assert np.size(ids_acquired) == nb_iterations
    assert len(np.unique(ids_acquired)) == nb_iterations
    return ids_acquired

# Run BO

In [11]:
nb_iterations = 150
nb_COFs_initialization = 3

In [12]:
for i, initializing_COFs in enumerate(init_cof_ids): 
    # check the length of each initializing set
    assert len(initializing_COFs) == nb_COFs_initialization
    print("run #: {}".format(i))
    
    # start timer for BO run
    start_time    = time.time()
    ###
    #  run BO search
    ###
    ids_acquired  = run_Bayesian_optimization(nb_iterations, initializing_COFs, verbose=True)
    
    ###
    #  post-run analysis
    ###
    elapsed_time  = time.time() - start_time
    y_acquired    = y[ids_acquired]
    y_maxes_acq   = get_y_maxes_acquired(y_acquired.detach().numpy())
    cost_acquired = build_cost(ids_acquired)
    acc_cost      = accumulated_cost(cost_acquired.detach().numpy())
        
    BO_iter_top_cof_acquired = np.argmax(y_acquired == max(y))
    print("iteration we acquire top COF = ", BO_iter_top_cof_acquired.item())
    
    top_cof_acc_cost = sum(cost_acquired[:BO_iter_top_cof_acquired]).item() 
    print("accumulated cost up to observation of top COF = ", top_cof_acc_cost, " [min]")
    
    ###
    #  Store SFBO results
    ###
    sfbo_res = dict({'ids_acquired': ids_acquired,
                     'y_acquired': y_acquired.detach().numpy(),
                     'y_max_acquired': y_maxes_acq,
                     'cost_acquired': cost_acquired.detach().numpy(),
                     'accumulated_cost': acc_cost / 60,
                     'nb_COFs_initialization': nb_COFs_initialization,
                     'BO_iter_top_cof_acquired': BO_iter_top_cof_acquired.item(),
                     'elapsed_time (min)':  elapsed_time / 60
                    })

    with open('search_results/{}/sfbo_results/sfbo_results_run_{}.pkl'.format(normalization, i), 'wb') as file:
        pickle.dump(sfbo_res, file)

run #: 0
Iter 10/100: 2.5316478673813574
Iter 20/100: 1.5976805610155178
Iter 30/100: 1.5335137562067445
Iter 40/100: 1.5103225146173305
Iter 50/100: 1.4670837577792153
Iter 60/100: 1.46410267330956
BO iteration  3
	acquired COF  521
	y =  15.766064256252303
Iter 10/100: 2.2821451376626243
Iter 20/100: 1.5767457678144892
Iter 30/100: 1.5160547021724815
Iter 40/100: 1.4776026924306396
Iter 50/100: 1.4418954556648254
Iter 60/100: 1.43763657751167
BO iteration  4
	acquired COF  523
	y =  14.017515356923804
Iter 10/100: 2.118271469591821
Iter 20/100: 1.5406069636537973
Iter 30/100: 1.4658872536471157
Iter 40/100: 1.4001012223371432
Iter 50/100: 1.3578769891536706
Iter 60/100: 1.3454021759424304
BO iteration  5
	acquired COF  524
	y =  6.895659242359536
Iter 10/100: 2.0287369141547815
Iter 20/100: 1.541780078511085
Iter 30/100: 1.4659487823993385
Iter 40/100: 1.4034512338980265
Iter 50/100: 1.3717580593803287
Iter 60/100: 1.361105079632785
Iter 70/100: 1.3618015872844431
Iter 80/100: 1.3601

Iter 20/100: 1.429028478903597
Iter 30/100: 1.3614301549302354
Iter 40/100: 1.2713704660939757
Iter 50/100: 1.170791985141159
BO iteration  42
	acquired COF  14
	y =  6.881047378855367
Iter 10/100: 1.5669156552054664
Iter 20/100: 1.4287022782510435
Iter 30/100: 1.3630345296394106
Iter 40/100: 1.2805961425355863
Iter 50/100: 1.2441196726974075
BO iteration  43
	acquired COF  515
	y =  6.237059454214897
Iter 10/100: 1.564915443037944
Iter 20/100: 1.4280230234141984
Iter 30/100: 1.3625088023252885
Iter 40/100: 1.2801281197458534
Iter 50/100: 1.2467900772603253
BO iteration  44
	acquired COF  149
	y =  4.870990027657603
Iter 10/100: 1.5626046190166525
Iter 20/100: 1.4269298032094793
Iter 30/100: 1.3612435080037733
Iter 40/100: 1.2792252398340007
Iter 50/100: 1.2486154006203505
BO iteration  45
	acquired COF  10
	y =  6.473829589979741
Iter 10/100: 1.5607194918637448
Iter 20/100: 1.4263514887445374
Iter 30/100: 1.3610154534330432
Iter 40/100: 1.280020433132811
Iter 50/100: 1.250579212370645

Iter 80/100: 1.2058886877964508
Iter 90/100: 1.2051956112787507
BO iteration  74
	acquired COF  451
	y =  2.7843374678631645
Iter 10/100: 1.5131796444574166
Iter 20/100: 1.3984405729030203
Iter 30/100: 1.3247586951550827
Iter 40/100: 1.264789376383358
Iter 50/100: 1.2283279626055488
Iter 60/100: 1.2039772202311516
Iter 70/100: 1.2031584488916516
Iter 80/100: 1.202458049973207
BO iteration  75
	acquired COF  450
	y =  3.890496901031045
Iter 10/100: 1.5119963318134042
Iter 20/100: 1.3976447635627007
Iter 30/100: 1.322634802820497
Iter 40/100: 1.2612240307847054
Iter 50/100: 1.2258649690069097
Iter 60/100: 1.2016294649772892
Iter 70/100: 1.2008071501791089
Iter 80/100: 1.2002387670218433
BO iteration  76
	acquired COF  36
	y =  2.8717389164600564
Iter 10/100: 1.5101388238235862
Iter 20/100: 1.3958654408563937
Iter 30/100: 1.319535858730366
Iter 40/100: 1.2576367532057053
Iter 50/100: 1.2225900640487841
Iter 60/100: 1.1984979330369878
Iter 70/100: 1.1975474451429378
Iter 80/100: 1.19713177

Iter 60/100: 1.1322599149604542
Iter 70/100: 1.1283887404776103
BO iteration  100
	acquired COF  60
	y =  3.8724205060110855
Iter 10/100: 1.481511956665914
Iter 20/100: 1.3686120048119117
Iter 30/100: 1.2692290220654674
Iter 40/100: 1.1843594730836995
Iter 50/100: 1.1485919239508402
Iter 60/100: 1.1298392497867786
Iter 70/100: 1.1260671832236708
BO iteration  101
	acquired COF  461
	y =  3.863653358562827
Iter 10/100: 1.4806311289499536
Iter 20/100: 1.3677256993579845
Iter 30/100: 1.2675800627635607
Iter 40/100: 1.1816430671356148
Iter 50/100: 1.1460391871211477
Iter 60/100: 1.1275555375694772
Iter 70/100: 1.12382527321168
Iter 80/100: 1.1236625872881618
BO iteration  102
	acquired COF  428
	y =  6.954408697894654
Iter 10/100: 1.479442580678323
Iter 20/100: 1.3665358509792416
Iter 30/100: 1.2653300466277586
Iter 40/100: 1.177027107937492
Iter 50/100: 1.1403317547976772
Iter 60/100: 1.1228496165800574
Iter 70/100: 1.1187620180196147
Iter 80/100: 1.118651173908134
Iter 90/100: 1.11821580

Iter 10/100: 1.4536660880657883
Iter 20/100: 1.3357244257507783
Iter 30/100: 1.2090938395725537
Iter 40/100: 1.08855566767103
Iter 50/100: 1.056805860011604
Iter 60/100: 1.0510148722875456
Iter 70/100: 1.0479239090044086
Iter 80/100: 1.0475224052381054
BO iteration  127
	acquired COF  359
	y =  2.616412984121879
Iter 10/100: 1.4525646048170393
Iter 20/100: 1.3344714022491844
Iter 30/100: 1.2068704713510987
Iter 40/100: 1.0847186113108322
Iter 50/100: 1.05307466497753
Iter 60/100: 1.0470568417267252
Iter 70/100: 1.044114959155093
Iter 80/100: 1.0437053136128238
BO iteration  128
	acquired COF  519
	y =  5.272175774230507
Iter 10/100: 1.4524147603642963
Iter 20/100: 1.3344217073063822
Iter 30/100: 1.2068105496732953
Iter 40/100: 1.0834003743365617
Iter 50/100: 1.0509643700877744
Iter 60/100: 1.0451838739572987
Iter 70/100: 1.0418562127816855
Iter 80/100: 1.0412930551179567
BO iteration  129
	acquired COF  22
	y =  3.836424483128883
Iter 10/100: 1.452109381533713
Iter 20/100: 1.3342218366

...

Iter 10/100: 1.4413244958310805
Iter 20/100: 1.3219115108983301
Iter 30/100: 1.1796799146496562
Iter 40/100: 1.0142916154022201
Iter 50/100: 0.9797547627120214
Iter 60/100: 0.9759241829403827
Iter 70/100: 0.9740009799970066
Iter 80/100: 0.9734148584987139
Iter 90/100: 0.9732545806243511
Iter 100/100: 0.973117662413749
BO iteration  148
	acquired COF  502
	y =  2.8316585429940866
Iter 10/100: 1.4404677668931605
Iter 20/100: 1.3208727523836308
Iter 30/100: 1.1778597236537232
Iter 40/100: 1.0105784856400757
Iter 50/100: 0.976332586728788
Iter 60/100: 0.9724911957357286
Iter 70/100: 0.9705830515423421
Iter 80/100: 0.9699908756892546
Iter 90/100: 0.9697818466607974
Iter 100/100: 0.9694950974208836
BO iteration  149
	acquired COF  452
	y =  2.6217427725930107
iteration we acquire top COF =  38
accumulated cost up to observation of top COF =  6708.504463338851  [min]
run #: 99
Iter 10/100: 2.5313406283525057
Iter 20/100: 1.5976486286198626
Iter 30/100: 1.533508398029386
Iter 40/100: 1.5101818

Iter 20/100: 1.442003193523965
Iter 30/100: 1.383647534923198
Iter 40/100: 1.318834277244177
Iter 50/100: 1.274069244560843
BO iteration  37
	acquired COF  234
	y =  12.493999419418008
Iter 10/100: 1.5801494166687622
Iter 20/100: 1.4350416309224288
Iter 30/100: 1.3703711397779201
Iter 40/100: 1.2915496587602944
Iter 50/100: 1.2692611840447632
BO iteration  38
	acquired COF  486
	y =  9.13840360931579
Iter 10/100: 1.5757362383190197
Iter 20/100: 1.431668621061721
Iter 30/100: 1.3658356644455711
Iter 40/100: 1.28607708444484
Iter 50/100: 1.1792069553209705
BO iteration  39
	acquired COF  65
	y =  3.715292189750088
Iter 10/100: 1.5736577686776296
Iter 20/100: 1.4319313521841255
Iter 30/100: 1.3665166650474552
Iter 40/100: 1.2853609125186842
Iter 50/100: 1.1785970328177737
BO iteration  40
	acquired COF  338
	y =  1.0959334177326576
Iter 10/100: 1.571765947967028
Iter 20/100: 1.4305529504652155
Iter 30/100: 1.3638900364728477
Iter 40/100: 1.2766798638440384
Iter 50/100: 1.180028701249765
B

BO iteration  70
	acquired COF  303
	y =  2.454825184564847
Iter 10/100: 1.5167175313017205
Iter 20/100: 1.3997621485118779
Iter 30/100: 1.3272935608748824
Iter 40/100: 1.269511219396499
Iter 50/100: 1.2306185541992176
Iter 60/100: 1.201452673039134
Iter 70/100: 1.1999754602459918
Iter 80/100: 1.1992740286550756
Iter 90/100: 1.1985262779657653
BO iteration  71
	acquired COF  88
	y =  3.561167963046627
Iter 10/100: 1.515228980525001
Iter 20/100: 1.3984906855015133
Iter 30/100: 1.3249329351888661
Iter 40/100: 1.2666236979776628
Iter 50/100: 1.2278068767830341
Iter 60/100: 1.199374140912171
Iter 70/100: 1.1977903286911769
Iter 80/100: 1.1971191678724897
Iter 90/100: 1.1964004410158158
BO iteration  72
	acquired COF  261
	y =  2.917267528486327
Iter 10/100: 1.5135310033393206
Iter 20/100: 1.3967609427534111
Iter 30/100: 1.3210134462962844
Iter 40/100: 1.261886608128286
Iter 50/100: 1.224057436186359
Iter 60/100: 1.196411880413791
Iter 70/100: 1.1948133007714663
Iter 80/100: 1.1941749243881

Iter 70/100: 1.1203326350359324
Iter 80/100: 1.1201457105147008
Iter 90/100: 1.1197106170698783
Iter 100/100: 1.1194329916640038
BO iteration  95
	acquired COF  106
	y =  4.333935334596865
Iter 10/100: 1.4840872120077269
Iter 20/100: 1.3701083025627936
Iter 30/100: 1.271095354002365
Iter 40/100: 1.1857283896327273
Iter 50/100: 1.1424111128924626
Iter 60/100: 1.1214006503763054
Iter 70/100: 1.1171645964294294
Iter 80/100: 1.1169633039299736
Iter 90/100: 1.116549667510095
Iter 100/100: 1.116280664865745
BO iteration  96
	acquired COF  10
	y =  6.473829589979741
Iter 10/100: 1.4835343435374937
Iter 20/100: 1.3696965273171542
Iter 30/100: 1.2703823297419703
Iter 40/100: 1.1870187423626428
Iter 50/100: 1.1536159648148931
Iter 60/100: 1.1322840691929772
Iter 70/100: 1.1291762515079031
BO iteration  97
	acquired COF  11
	y =  4.802045291586816
Iter 10/100: 1.482882666326499
Iter 20/100: 1.3692437360505032
Iter 30/100: 1.269378720067393
Iter 40/100: 1.1849752349500078
Iter 50/100: 1.1511764949

Iter 10/100: 1.4552927978585188
Iter 20/100: 1.338607319454508
Iter 30/100: 1.2140264850365734
Iter 40/100: 1.0939480737011547
Iter 50/100: 1.0634427897311576
Iter 60/100: 1.0567498760663845
Iter 70/100: 1.054478355483384
Iter 80/100: 1.0537704039907478
BO iteration  129
	acquired COF  325
	y =  6.7022303871119275
Iter 10/100: 1.4545255137081254
Iter 20/100: 1.3377294644430087
Iter 30/100: 1.2123873863622012
Iter 40/100: 1.090927403342474
Iter 50/100: 1.0602818878838676
Iter 60/100: 1.0540881764689722
Iter 70/100: 1.0518877540767178
Iter 80/100: 1.05116320158148
BO iteration  130
	acquired COF  280
	y =  4.1685963900813
Iter 10/100: 1.4539455551518567
Iter 20/100: 1.3371897106368957
Iter 30/100: 1.2112571747984187
Iter 40/100: 1.0882174650586744
Iter 50/100: 1.057270186225304
Iter 60/100: 1.051129024090814
Iter 70/100: 1.0490113131379448
Iter 80/100: 1.0482613906163765
BO iteration  131
	acquired COF  155
	y =  8.154222204607914
Iter 10/100: 1.4525223521998956
Iter 20/100: 1.3354074080

# Random Search

In [13]:
nb_runs = 1000

rs_res = dict()
rs_res['ids_acquired']     = []
rs_res['cost_acquired']    = []
rs_res['accumulated_cost'] = []

for r in range(nb_runs):
    rs_ids_acquired     = np.random.choice(range(nb_COFs), replace=False, size=nb_iterations)
    rs_cost_acquired    = build_cost(rs_ids_acquired)
    rs_accumulated_cost = accumulated_cost(rs_cost_acquired)
    rs_res['ids_acquired'].append(rs_ids_acquired)
    rs_res['cost_acquired'].append(rs_cost_acquired)
    rs_res['accumulated_cost'].append(rs_accumulated_cost / 60)

In [14]:
def test_rs(rs_res):
    for a in np.random.choice(nb_runs, replace=False, size=7):
        # check that the lengths 
        assert len(rs_res['ids_acquired'][a]) == nb_iterations
        assert all([cof_id in range(nb_COFs) for cof_id in rs_res['ids_acquired'][a]])
    return

test_rs(rs_res)

In [15]:
# get y_max acquired up to iteration i for i = 1,2,...
def y_max(rs_ids_acquired):
    y_max_mu      = np.zeros(nb_iterations)
    y_max_sig_bot = np.zeros(nb_iterations)
    y_max_sig_top = np.zeros(nb_iterations)
    # element i of these will be y max at BO iter i
    
    for i in range(1, nb_iterations+1):
        # max value acquired up to this point
        y_maxes = np.array([max(y[rs_ids_acquired[r][:i]]) for r in range(nb_runs)])
        assert np.size(y_maxes) == nb_runs
        y_max_mu[i-1]      = np.mean(y_maxes)
        y_max_sig_bot[i-1] = np.std(y_maxes[y_maxes < y_max_mu[i-1]])
        y_max_sig_top[i-1] = np.std(y_maxes[y_maxes > y_max_mu[i-1]])
    return y_max_mu, y_max_sig_bot, y_max_sig_top

# rs_mean, rs_lower_bound, rs_upper_bound = y_max(rs_res)
y_rs_max_mu, y_rs_max_sig_bot, y_rs_max_sig_top = y_max(rs_res['ids_acquired'])

In [16]:
###
#  Store Random Search Results
###
random_search_results = dict({'ids_acquired': rs_res['ids_acquired'],
                             'y_rs_max_mu': y_rs_max_mu,
                             'y_rs_max_sig_bot': y_rs_max_sig_bot,
                             'y_rs_max_sig_top': y_rs_max_sig_top,
                             'cost_acquired': rs_res['cost_acquired'],
                             'accumulated_cost': rs_res['accumulated_cost']
                             })

with open('search_results/{}/random_search_results.pkl'.format(normalization), 'wb') as file:
    pickle.dump(random_search_results, file)